In [1]:
import pandas as pd
import numpy as np

import os
import gc
import warnings

warnings.filterwarnings("ignore", category=UserWarning)
warnings.filterwarnings("ignore", category=FutureWarning)

In [2]:
# make ready for classification
from sklearn.preprocessing import OneHotEncoder, LabelEncoder
ohe = OneHotEncoder()
le = LabelEncoder()

In [3]:
root = './data/'

og = pd.read_csv(root+'to_predict_problem_1.csv').drop('YEAR', axis=1)
#og['MAGIC_KEY'] = le.fit_transform(og['MAGIC_KEY'])

y_meat = og['MEAT']
X_meat = og.drop(['MILK', 'MEAT'], axis=1)

y_milk = og['MILK'].rename('P_MILK')
X_milk = og.drop(['MILK', 'MEAT'], axis=1)

problem_1 = pd.read_csv(root+'problem 1.csv')

In [62]:
X_meat.head(3)

MAGIC_KEY  DAY  MONTH
0      53697    1      2
1      52770    1      2
2      43983    1      2

In [63]:
y_meat.head(3)

0    0.0
1    0.0
2    0.0
Name: MEAT, dtype: float64

In [64]:
X_milk.nunique()

MAGIC_KEY    58689
DAY             31
MONTH            2
dtype: int64

In [65]:
y_meat

0         0.0
1         0.0
2         0.0
3         0.0
4         0.0
         ... 
108190    2.7
108191    2.7
108192    2.2
108193    2.5
108194    2.2
Name: MEAT, Length: 108195, dtype: float64

### APPROACH 1

In [66]:
# for meat data
X_meat_cl = X_meat.copy()
y_meat_enc = y_meat.copy()

y_meat_enc = y_meat_enc.apply(lambda x : 1 if x > 0 else 0)

# for milk set
X_milk_cl = X_milk.copy()
y_milk_enc = y_milk.copy()

y_milk_enc = y_milk_enc.apply(lambda x : 1 if x > 0 else 0)

### 1 = Y, 0 = NO

In [67]:
y_meat_enc

0         0
1         0
2         0
3         0
4         0
         ..
108190    1
108191    1
108192    1
108193    1
108194    1
Name: MEAT, Length: 108195, dtype: int64

In [66]:
from sklearn.ensemble import HistGradientBoostingClassifier, HistGradientBoostingRegressor, GradientBoostingClassifier
from xgboost import XGBRegressor, XGBClassifier
from lightgbm import LGBMRegressor, LGBMClassifier
from catboost import CatBoostRegressor, CatBoostClassifier
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.gaussian_process import GaussianProcessClassifier
from sklearn.ensemble import AdaBoostClassifier

from sklearn.model_selection import train_test_split

class ClassifierV1:
    def __init__(self):
        self.models = {
            'GBC': GradientBoostingClassifier(),
            'ABC': AdaBoostClassifier(),
            'SVC': SVC(),
            'KNC': KNeighborsClassifier(),
            'GPC': GaussianProcessClassifier(),
            'XGBC': XGBClassifier(),
            'LGBC': LGBMClassifier(),
            'CBC': CatBoostClassifier(),
            'HBC': HistGradientBoostingClassifier()
        }
        
        self.best_model = None
        self.score = {} 

    def fit(self, X, y):
        X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.15, random_state=42)
        
        for name, model in self.models.items():
            print(model)
            # print(X_train.shape, y_train.shape)
            # model.fit(X_train, y_train)
            # preds = model.predict(X_val)
            # 
            # self.score[name] = accuracy_score(y_val, preds) 
            
    def predict(self, X, model=None):
        if model:
            return self.models[model].predict(X)

        return {name: model.predict(X) for name, model in self.models.items()}
    
    def get_score(self):
        return self.score

class RegressorV1:
    def __init__(self):
        self.models = {
            'HistGradientBoostingRegressor': HistGradientBoostingRegressor(),
            'XGBRegressor': XGBRegressor(),
            'LGBMRegressor': LGBMRegressor(),
            'CatBoostRegressor': CatBoostRegressor()
        }

    def fit(self, X, y):
        for model in self.models.values():
            print(model)

    def predict(self, X, model=None):
        if model:
            return self.models[model].predict(X)

        return {name: model.predict(X) for name, model in self.models.items()}

In [67]:
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import accuracy_score, f1_score, confusion_matrix, roc_auc_score, recall_score, precision_score

class TrainClassifier:
    def __init__(self, model, X, y, n_splits=5):
        self.model = model
        self.X = X
        self.y = y
        self.n_splits = n_splits
        self.f1_scores = []
        self.log_losses = []
        self.accuracy_scores = []
        self.recall = []
        self.roc_auc = []
        self.precision = []

    def train(self):
        kf = StratifiedKFold(n_splits=self.n_splits, shuffle=True)
        f1_scores = []
        log_losses = []
        accuracy_scores = []
        roc_auc = []
        recall = []
        precision = []

        for train_index, test_index in kf.split(self.X):
            X_train, X_test = self.X.iloc[train_index], self.X.iloc[test_index]
            y_train, y_test = self.y.iloc[train_index], self.y.iloc[test_index]

            self.model.fit(X_train, y_train)
            preds = self.model.predict(X_test)

            f1_scores.append(f1_score(y_test, preds))
            log_losses.append((y_test, preds))
            accuracy_scores.append(accuracy_score(y_test, preds))
            recall.append(recall_score(y_test, preds))
            precision.append(precision_score(y_test, preds))
            roc_auc.append(roc_auc_score(y_test, preds))
            

        self.f1_scores = f1_scores
        self.log_losses = log_losses
        self.accuracy_scores = accuracy_scores
        self.recall = recall
        self.precision = precision
        self.roc_auc = roc_auc

    def get_scores(self):
        return {
            'f1_scores': self.f1_scores,
            'log_losses': self.log_losses,
            'accuracy_scores': self.accuracy_scores,
            'roc_auc': self.roc_auc,
            'recall': self.recall,
            'pricision': self.precision
        }


In [68]:
classifierV1_meat = ClassifierV1()
classifierV1_meat.fit(X_meat_cl, y_meat_enc)

NameError: name 'X_meat_cl' is not defined

In [74]:
classifierV1_milk = ClassifierV1()
classifierV1_milk.fit(X_milk_cl, y_milk_enc)

GradientBoostingClassifier()
AdaBoostClassifier()
SVC()
KNeighborsClassifier()
GaussianProcessClassifier()
XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, device=None, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=None, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=None, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimators=None, n_jobs=None,
              num_parallel_tree=None, random_state=None, ...)
LGBMClassifier()
HistGradientBoostingClassifier()


In [117]:
X_train, X_val, y_train, y_val = train_test_split(X_meat_cl, y_meat_enc, test_size=0.2, random_state=42)

model_meat = CatBoostClassifier(
    learning_rate = 0.005, 
    l2_leaf_reg=0.5, 
    early_stopping_rounds=5, 
    iterations=60000, 
    loss_function="Logloss", 
    task_type="GPU"
)
model_meat.fit(X_train, y_train)
preds = model_meat.predict(X_val)
print(accuracy_score(y_val, preds))
print(f1_score(y_val, preds))

0:	learn: 0.6898124	total: 8.92ms	remaining: 8m 55s
1:	learn: 0.6865262	total: 12ms	remaining: 6m
2:	learn: 0.6832613	total: 14.8ms	remaining: 4m 55s
3:	learn: 0.6800827	total: 16.6ms	remaining: 4m 9s
4:	learn: 0.6768885	total: 19.4ms	remaining: 3m 52s
5:	learn: 0.6737834	total: 21.5ms	remaining: 3m 34s
6:	learn: 0.6706694	total: 29ms	remaining: 4m 8s
7:	learn: 0.6676522	total: 33.8ms	remaining: 4m 13s
8:	learn: 0.6646110	total: 45.2ms	remaining: 5m 1s
9:	learn: 0.6616162	total: 47.4ms	remaining: 4m 44s
10:	learn: 0.6587444	total: 49.6ms	remaining: 4m 30s
11:	learn: 0.6558012	total: 52.4ms	remaining: 4m 21s
12:	learn: 0.6529515	total: 54.1ms	remaining: 4m 9s
13:	learn: 0.6500901	total: 56.2ms	remaining: 4m 1s
14:	learn: 0.6472909	total: 58.1ms	remaining: 3m 52s
15:	learn: 0.6445052	total: 60.1ms	remaining: 3m 45s
16:	learn: 0.6417306	total: 62.8ms	remaining: 3m 41s
17:	learn: 0.6390365	total: 64.7ms	remaining: 3m 35s
18:	learn: 0.6363609	total: 66.5ms	remaining: 3m 29s
19:	learn: 0.633

In [118]:
X_train, X_val, y_train, y_val = train_test_split(X_milk_cl, y_milk_enc, test_size=0.2, random_state=42)

model_milk = CatBoostClassifier(
    learning_rate = 0.005, 
    l2_leaf_reg=0.5, 
    early_stopping_rounds=5, 
    iterations=60000, 
    loss_function="Logloss", 
    task_type="GPU"
)
model_milk.fit(X_train, y_train)
preds = model_milk.predict(X_val)
print(accuracy_score(y_val, preds))
print(f1_score(y_val, preds))

0:	learn: 0.6928219	total: 3.15ms	remaining: 3m 8s
1:	learn: 0.6924847	total: 5.89ms	remaining: 2m 56s
2:	learn: 0.6921511	total: 8.62ms	remaining: 2m 52s
3:	learn: 0.6918345	total: 11.3ms	remaining: 2m 49s
4:	learn: 0.6915260	total: 14ms	remaining: 2m 48s
5:	learn: 0.6912263	total: 16.7ms	remaining: 2m 47s
6:	learn: 0.6909220	total: 19.3ms	remaining: 2m 45s
7:	learn: 0.6906209	total: 22ms	remaining: 2m 44s
8:	learn: 0.6903199	total: 24.6ms	remaining: 2m 44s
9:	learn: 0.6900222	total: 27.3ms	remaining: 2m 43s
10:	learn: 0.6897486	total: 29.4ms	remaining: 2m 40s
11:	learn: 0.6894617	total: 32.1ms	remaining: 2m 40s
12:	learn: 0.6891709	total: 34.7ms	remaining: 2m 40s
13:	learn: 0.6888943	total: 37.4ms	remaining: 2m 40s
14:	learn: 0.6886136	total: 40.2ms	remaining: 2m 40s
15:	learn: 0.6883298	total: 42.9ms	remaining: 2m 40s
16:	learn: 0.6880562	total: 45.6ms	remaining: 2m 40s
17:	learn: 0.6877780	total: 48.3ms	remaining: 2m 41s
18:	learn: 0.6874928	total: 51.1ms	remaining: 2m 41s
19:	lear

In [226]:
problem_1 = pd.read_csv('./data/problem 1.csv')
problem_1['MAGIC_KEY'] = le.fit_transform(problem_1['MAGIC_KEY'])

submission = og[(og['DAY'] <= 15) & og['MAGIC_KEY'].isin(problem_1['MAGIC_KEY'])].drop(['MEAT', 'MILK'], axis=1)
submission['MONTH'] = 3

In [120]:
meat_predict = model_meat.predict(submission)
milk_predict = model_milk.predict(submission)

In [227]:
submission['P_MILK'] = milk_predict
submission['P_MEAT'] = meat_predict
submission['PURCHASE'] = 'N' 
submission

MAGIC_KEY  DAY  MONTH  P_MILK  P_MEAT PURCHASE
0           53697    1      3       1       1        N
1           52770    1      3       1       1        N
2           43983    1      3       1       1        N
3           48454    1      3       1       1        N
4           57395    1      3       1       1        N
...           ...  ...    ...     ...     ...      ...
108189      56123    3      3       1       1        N
108190       7263    3      3       0       1        N
108191      43877    3      3       0       1        N
108192      50041    5      3       1       1        N
108193      50041    5      3       1       1        N

[61015 rows x 6 columns]

In [263]:
ff_submission = submission.groupby(['MAGIC_KEY', 'DAY']).agg(
    {
        'P_MILK': 'max',
        'P_MEAT': 'max'
    }
).reset_index()

In [264]:
ff_submission

MAGIC_KEY  DAY  P_MILK  P_MEAT
0              0    5       1       1
1              1   13       0       1
2              1   14       0       1
3              2    7       1       1
4              4    2       1       1
...          ...  ...     ...     ...
58909      58685    4       1       1
58910      58685   12       1       1
58911      58687   10       0       1
58912      58687   11       1       1
58913      58688    6       1       1

[58914 rows x 4 columns]

In [265]:
ff_submission['PURCHASE'] = ff_submission.apply(lambda row: 'Y' if row['P_MILK'] == 1 or row['P_MEAT'] == 1 else 'N', axis=1)

# Create the final DataFrame with 'CUSTOMER_KEY' and 'PURCHASE'
final_df = ff_submission[['MAGIC_KEY', 'PURCHASE']]

In [266]:
final_df

MAGIC_KEY PURCHASE
0              0        Y
1              1        Y
2              1        Y
3              2        Y
4              4        Y
...          ...      ...
58909      58685        Y
58910      58685        Y
58911      58687        Y
58912      58687        Y
58913      58688        Y

[58914 rows x 2 columns]

In [267]:
final_df = final_df.drop_duplicates()
final_df

MAGIC_KEY PURCHASE
0              0        Y
1              1        Y
3              2        Y
4              4        Y
5              5        Y
...          ...      ...
58906      58682        Y
58907      58684        Y
58909      58685        Y
58911      58687        Y
58913      58688        Y

[40204 rows x 2 columns]

In [268]:
final_df['MAGIC_KEY'] = final_df['MAGIC_KEY'].map(pd.DataFrame(le.classes_).to_dict()[0])

/tmp/ipykernel_9570/2853445572.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  final_df['MAGIC_KEY'] = final_df['MAGIC_KEY'].map(pd.DataFrame(le.classes_).to_dict()[0])


In [269]:
to_append = list(set(problem_1.MAGIC_KEY.map(pd.DataFrame(le.classes_).to_dict()[0])).difference(set(final_df.MAGIC_KEY)))
final_df = pd.concat([final_df, pd.DataFrame({'MAGIC_KEY':to_append, 'PURCHASE':'N'})])

In [274]:
final_df.to_csv('./submissions/submission.csv', index=False)

### APPROACH 2

In [81]:
 # FIRST 15 DAYS OF EVERY MONTH
date = pd.DataFrame({'DATE': pd.date_range(start='1/1/2019', end='2/15/2019', freq='D')})
date['DATE'] = pd.to_datetime(date['DATE'], format='%Y-%m-%d')

date['DAY'] = date['DATE'].dt.day
date['MONTH'] = date['DATE'].dt.month
date = date[(date['DAY'] <= 15)]

In [82]:
X_2_train = date[['DAY', 'MONTH', 'DATE']]
X_2_train = pd.concat([X_2_train]*problem_1.MAGIC_KEY.nunique(), ignore_index=True)

In [83]:
X_2_train['MAGIC_KEY'] = problem_1.MAGIC_KEY.repeat(30).values

In [84]:
X_2_train.nunique()

DAY             15
MONTH            2
DATE            30
MAGIC_KEY    58689
dtype: int64

In [85]:
X_2_train = pd.merge(X_2_train, og, on=['MAGIC_KEY', 'MONTH', 'DAY'], how='left')

In [86]:
X_2_train.fillna(0, inplace=True)
X_2_train.nunique()

DAY             15
MONTH            2
DATE            30
MAGIC_KEY    58689
MEAT            15
MILK            17
dtype: int64

In [87]:
X_2_train['MAGIC_KEY'] = le.fit_transform(X_2_train['MAGIC_KEY'])

In [89]:
# probability of purchase
X_2_train['PURCHASE_Q'] = X_2_train['MEAT'] + X_2_train['MILK']
X_2_train['PURCHASE'] = X_2_train['PURCHASE_Q'].apply(lambda x: 1 if x > 0 else 0)

In [90]:
X_2_train[X_2_train['MAGIC_KEY'] == 8546]

DAY  MONTH       DATE  MAGIC_KEY  MEAT  MILK  PURCHASE_Q  PURCHASE
1352832    1      1 2019-01-01       8546   0.0   0.0         0.0         0
1352833    2      1 2019-01-02       8546   0.0   0.0         0.0         0
1352834    3      1 2019-01-03       8546   0.0   0.0         0.0         0
1352835    4      1 2019-01-04       8546   0.0   0.0         0.0         0
1352836    5      1 2019-01-05       8546   0.0   0.0         0.0         0
1352837    6      1 2019-01-06       8546   0.0   0.0         0.0         0
1352838    7      1 2019-01-07       8546   0.0   0.0         0.0         0
1352839    8      1 2019-01-08       8546   0.0   0.0         0.0         0
1352840    9      1 2019-01-09       8546   0.0   0.0         0.0         0
1352841   10      1 2019-01-10       8546   0.0   0.0         0.0         0
1352842   11      1 2019-01-11       8546   0.0   0.0         0.0         0
1352843   12      1 2019-01-12       8546   0.0   0.0         0.0         0
1352844   13      1 2019-01-13       8546   0.0   0.0         0.0         0
1352845   14      1 2019-01-14       8546   2.2   8.0        10.2         1
1352846   15      1 2019-01-15       8546   0.0   0.0         0.0         0
1352847    1      2 2019-02-01       8546   0.0   0.0         0.0         0
1352848    2      2 2019-02-02       8546   0.0   0.0         0.0         0
1352849    3      2 2019-02-03       8546   0.0   0.0         0.0         0
1352850    4      2 2019-02-04       8546   0.0   0.0         0.0         0
1352851    5      2 2019-02-05       8546   0.0   0.0         0.0         0
1352852    6      2 2019-02-06       8546   0.0   0.0         0.0         0
1352853    7      2 2019-02-07       8546   0.0   0.0         0.0         0
1352854    8      2 2019-02-08       8546   0.0   0.0         0.0         0
1352855    9      2 2019-02-09       8546   0.0   0.0         0.0         0
1352856   10      2 2019-02-10       8546   0.0   0.0         0.0         0
1352857   11      2 2019-02-11       8546   0.0   0.0         0.0         0
1352858   12      2 2019-02-12       8546   0.0   0.0         0.0         0
1352859   13      2 2019-02-13       8546   0.0   0.0         0.0         0
1352860   14      2 2019-02-14       8546   0.0   0.0         0.0         0
1352861   15      2 2019-02-15       8546   2.2   8.0        10.2         1

In [139]:
train_m1 = X_2_train[X_2_train.MONTH == 1].reset_index().drop('index', axis=1)
train_m2 = X_2_train[X_2_train.MONTH == 2].reset_index().drop('index', axis=1)

In [142]:
train_m2['prev_purchase'] = train_m1['PURCHASE']
train_m2.loc[:, 'prev_month'] = 1

In [150]:
train_m2.drop(['DATE', 'PURCHASE_Q', 'MEAT', 'MILK'], axis=1, inplace=True)
train_m2.nunique()

KeyError: "['DATE', 'PURCHASE_Q', 'MEAT', 'MILK'] not found in axis"

In [171]:
to_predict = None
to_predict = train_m2[train_m2.columns]
to_predict.drop(['PURCHASE'], axis=1, inplace=True)
to_predict.prev_purchase = train_m2['PURCHASE']

In [173]:
to_predict.drop(['MONTH', 'prev_month'], axis=1, inplace=True)
to_predict.nunique()

DAY                 15
MAGIC_KEY        58689
prev_purchase        2
dtype: int64

In [175]:
from catboost import CatBoostClassifier

X_train, X_val, y_train, y_val = train_test_split(train_m2[['DAY', 'MAGIC_KEY', 'prev_month']], train_m2['PURCHASE'], test_size=0.2, shuffle=True, random_state=42)

model = CatBoostClassifier(
    learning_rate = 0.005, 
    l2_leaf_reg=0.5, 
    early_stopping_rounds=5, 
    iterations=10000, 
    loss_function="Logloss", 
    task_type="GPU"
)

model.fit(X_train, y_train)

0:	learn: 0.6853927	total: 20.7ms	remaining: 3m 26s
1:	learn: 0.6777509	total: 41.3ms	remaining: 3m 26s
2:	learn: 0.6702152	total: 61.3ms	remaining: 3m 24s
3:	learn: 0.6627841	total: 81.2ms	remaining: 3m 22s
4:	learn: 0.6554574	total: 102ms	remaining: 3m 23s
5:	learn: 0.6482371	total: 120ms	remaining: 3m 20s
6:	learn: 0.6411188	total: 140ms	remaining: 3m 19s
7:	learn: 0.6341015	total: 159ms	remaining: 3m 18s
8:	learn: 0.6271832	total: 178ms	remaining: 3m 17s
9:	learn: 0.6203618	total: 197ms	remaining: 3m 16s
10:	learn: 0.6136378	total: 228ms	remaining: 3m 27s
11:	learn: 0.6070100	total: 244ms	remaining: 3m 22s
12:	learn: 0.6004771	total: 263ms	remaining: 3m 21s
13:	learn: 0.5940398	total: 282ms	remaining: 3m 20s
14:	learn: 0.5876934	total: 301ms	remaining: 3m 20s
15:	learn: 0.5814379	total: 319ms	remaining: 3m 19s
16:	learn: 0.5752727	total: 338ms	remaining: 3m 18s
17:	learn: 0.5691997	total: 356ms	remaining: 3m 17s
18:	learn: 0.5632153	total: 375ms	remaining: 3m 16s
19:	learn: 0.55731

In [176]:
preds = model.predict(X_val)
print(accuracy_score(y_val, preds))
print(f1_score(y_val, preds))
print(roc_auc_score(y_val, preds))

0.9642128938086773
0.0
0.5


In [178]:
predicted = model.predict(to_predict)

In [179]:
to_predict['PURCHASE'] = predicted

In [180]:
to_predict['PURCHASE'] = to_predict['PURCHASE'].apply(lambda x: 'Y' if x == 1 else 'N')

In [181]:
to_predict.drop_duplicates()


DAY  MAGIC_KEY  prev_purchase PURCHASE
0         1       4878              0        N
1         2       4878              0        N
2         3       4878              0        N
3         4       4878              0        N
4         5       4878              0        N
...     ...        ...            ...      ...
880337   11      40856              0        N
880338   12      40856              0        N
880339   13      40856              0        N
880340   14      40856              0        N
880341   15      40856              1        N

[880335 rows x 4 columns]

In [183]:
model.get_feature_importance()

array([40.29044787, 59.70955213,  0.        ])